In [17]:
## Example of Two-Hierarchy Storage System

candidates_info = {
    "C000001":{
        "Name":"Bob",
        "Country&City":"003004",
        "Work_Autho":"Citizen",
        "Degree&Major":"MIT Master of Science in Computer Science | USC Bachelor in Business Analytics",
        "YOE&Industry":"Google 2016.3.21-2018.7.12 Software Engineer | 2018.9 - 2021.12 TikTok Analyst",
        "skills":"Python, JAVA, SQL, Data Structure, Web Scraping ...",
        "working_experiences":"help company to build the pipeline of the work. help compant to build a recommendation system and data cleaning.",
        "project_experiences":"construct a dashboard that includes all the information presented in the spread sheet. maintain a system the helps prople to make the choice.",
        "posting_history":["A000001","A000003"]
            },
    "C000002":{
        "Name":"Tim",
        "Country&City":"001002",
        "Work_Autho":"F-1",
        "Current_Status":"out of work",
        "Degree&Major":"Stanford Bachelor of Science in Data Science| MIT Master in Finance",
        "YOE&Industry":"2021/9- Amazon Data Analyst",
        "skills":"Python, JAVA, SQL, Statistics",
        "working_experiences":"TikTok...",
        "project_experiences":"Fraud Analysis to help NY city government to identify the potential risk",
        "posting_history":["A000002","A000004"]
            },
}

In [2]:
import json
with open("./parse from csv/try.json","r") as f:
    data = json.load(f)

data

{'10000': {'name': 'lindsey weedon',
  'Country&City': 44,
  'Work_Autho': 'None',
  'Degree&Major': 'aston business school bachelor business & management',
  'YOE&Industry': 'google product marketing manager, emea 2020-09-01 2021-01-02|google growth manager 2020-01-01 2020-12-31|google national partnership manager, grow with google uk 2019-08-01 2020-08-31|the golden chopsticks awards marketing manager (contractor) 2018-09-01 2019-07-01|just eat marketing manager - events & sponsorship 2017-08-01 2018-08-31|harli jaigo (baby & toddler clothing) founder 2015-04-01 2017-08-01|deloitte internal communications & events manager 2016-08-01 2017-08-01|lavazza coffee marketing manager (contractor) 2015-06-01 2015-08-01|lavazza coffee in home marketing specialist 2010-06-01 2012-10-01|ssp limited promotions manager 2014-05-01 2014-09-01|new look retailers brand coordinator 2012-10-01 2014-05-01',
  'skills': 'None',
  'working_experiences': 'marketing (contractor)\r\n\r\nresponsibilities: glob

In [19]:
import pandas as pd
import re
import nltk
from nltk.corpus import stopwords
from datetime import datetime
import spacy

nlp = spacy.load("en_core_web_sm")
lemmatizer = nlp.get_pipe("lemmatizer")

class clean_candidate_profile():

    cleaned_info = {}

    def __init__(self,data,id):
        self.data = data
        self.id = id
    
    @ staticmethod
    def get_degree_info(s):
        '''# TODO: (1) this classification system should be double checked and extended'''
        degree_info={"primary school":1,
        "special education":2,
        "ged":3,
        "general education":3,
        "secondary":4,
        "junior high school":5,
        "high school":6,
        "certification":7,
        "vocational":8,
        "college":9,
        "HND":10,
        "HNC":10,
        "higher national":10,
        "associate":11,
        "international":12,
        "bachelor":13,
        "bs":13,
        "ba":13,
        "master":14,
        "ms":14,
        "ma":14,
        "mba":14,
        "intermediate graduate":15,
        "professional":15,
        "post professional":16,
        "doctor":17,
        "phd":17,
        "md":17,
        "post doctor":18}
        degree_num = 0
        new_s = s
        for degree_level in degree_info.keys():
            if degree_level in s:
                new_s = new_s.replace(degree_level,"")
                degree_num = max(degree_info[degree_level],degree_num)
            else:
                continue
        new_s = re.sub("[a-z] ","",new_s)
        return degree_num, new_s
    
    def get_major_info(self,s):
        '''# TODO: (2) The major system should be extended! How to deal if not match?'''
        major = []
        df_subject = pd.read_excel("temp_merged_major.xlsx")
        subject_list = list(df_subject['major'])
        # if exists, find it out directly
        for subject in subject_list:
            if subject in s:
                major.append(subject)
            else:
                continue
        if major == []:
            major.append(self.get_degree_info(s)[1])
        return major

    def clean_degree_and_major(self):
        final_output = []
        s_degree = self.data[self.id]["Degree&Major"]
        if s_degree == "None":
            return []
        else:
            # split the sentences and store in the list (can be used for deducting the classification of words)
            sentences = s_degree.split("|")
            # store cleaned sentences
            corpus = []
            # clean data
            for i in range(len(sentences)):
                review = sentences[i].replace("etc.","").replace("e.g.","").replace("i.e.","")
                # delete the label (can be extended if meet new format)
                review = re.sub('[1-9][\.)]'," ",review)
                review = re.sub('[^1-9a-zA-Z+-]'," ",review)
                review = review.lower()
                review = review.split()
                # delete stop words and transfer words to unified format
                review = [word for word in review if not word in set(stopwords.words("english"))]
                review = " ".join(review)
                doc = nlp(review)
                corpus.append(" ".join([token.lemma_ for token in doc]))
            for element in corpus:
                final_output.append([self.get_degree_info(element)[0],self.get_major_info(element)])
        return final_output
    
    @staticmethod
    def recog_and_calculate_time(s):
        # [1-9]\d{3}-(0[1-9]|1[0-2])-(0[1-9]|[1-2][0-9]|3[0-1])
        '''# TODO: (3) confirm the normal format of datetime!'''
        # this part of code can deal with 
        # YYYY-MM-DD,YYYY-M-DD,YYYY-MM-D,YYYY/MM/DD,YYYY/M/DD,YYYY/MM/D,YYYY-MM,YYYY-M,YYYY/MM,YYYY/M
        # MM-DD-YYYY,M-DD-YYYY,MM-D-YYYY,MM/DD/YYYY,M/DD/YYYY,MM/D/YYYY,M-YYYY,MM-YYYY,MM/YYYY,M/YYYY
        # YYYY.MM.DD,YYYY.M.DD,YYYY.MM.D,YYYY.MM,YYYY.M,MM.YYYY,M.YYYY,MM.DD.YYYY,M.DD.YYYY,MM.D.YYYY
        s = re.sub('[^0-9-./]'," ",s).strip()
        new_s = []
        for single_word in s.split():
            if "-" in single_word and len(single_word)>=6:
                new_s.append(single_word)
            else:
                continue
        s = " ".join(new_s)
        s = re.sub("[^0-9]*-[^0-9]*","",s)
        rexp = re.compile(r'(\d{4}(-|/|.)*(0[1-9]|1[0-2]|[1-9])*(-|/|.)*(0[1-9]|[12][0-9]|3[01]|[1-9])*)|(0[1-9]|1[0-2]|[1-9])*(-|/|.)*(0[1-9]|[12][0-9]|3[01]|[1-9])*(-|/|.)*(\d{4})')
        it = rexp.finditer(s)
        date_info = []
        for single_ele in it:
            l = single_ele.group().split()
            for i in l:
                date_info.append(pd.to_datetime(i))
        if len(date_info)==2:
            time_len = (date_info[1]-date_info[0]).days
        elif len(date_info)==0:
            return 0
        else:
            time_len = (datetime.now()-date_info[0]).days
        return time_len
    
    @staticmethod
    def recog_position(s):
        # it is better to label industries or connect industries with majors
        '''# TODO: (3) If it is accurate using key words to find related majors'''
        title_final = []
        position_name = pd.read_excel("title_final.xlsx")
        title = position_name["job_title"]
        # can find, extract directly
        for i in title:
            if i in s:
                title_final.append(i)
        if len(title_final) ==1:
            return title_final
        elif len(title_final) >1:
            len_position = 0
            for each_position in title_final:
                if len(each_position)>len_position:
                    title_final = [each_position]
                    len_position = len(each_position)
                else:
                    continue
            return title_final
        else:
            # can't find, find related
            for remaning_word in s.split():
                for i in title:
                    if remaning_word in i and remaning_word!= "science" and remaning_word!= "officier" and remaning_word != "manager" and remaning_word!= "associates": # could extend unrelated words, but it would be better if we can use labels!!!
                        title_final.append(i)
                    else:
                        continue
            return title_final
            
    def clean_yoe_industry(self):
        s_yoe = self.data[self.id]["YOE&Industry"]
        yoe_industry_info = []
        if s_yoe == "None":
            return []
        else:
            s_yoe_list = s_yoe.split("|")
            # store cleaned sentences
            cleaned_yoe_industry = []
            # clean data
            for i in s_yoe_list:
                review = i.replace("etc.","").replace("e.g.","").replace("i.e.","")
                # only keep letters, + and - in the original passage
                review = re.sub('[^0-9a-zA-Z+-./]'," ",review)
                review = re.sub("[^0-9][-|/|.][^0-9]","",review)
                review = re.sub(r"[' '|A-Za-z]\d{1,}[A-Za-z|' ']","",review)
                review = re.sub(r"[^-0-9]\d{1,2}-\d{1,2}[^-0-9]","",review)
                # review = review.replace("-"," ")
                review = review.replace(" one "," ").replace(" two "," ").replace(" three "," ").replace(" four "," ").replace(" five "," ").replace(" six "," ").replace(" seven "," ").replace(" eight "," ").replace(" nine "," ").replace(" ten "," ")
                review = review.lower()
                review = review.split()
                # delete stop words and transfer words to unified format
                review = [word for word in review if not word in set(stopwords.words("english"))]
                review = " ".join(review)
                cleaned_yoe_industry.append(review)
            for i in cleaned_yoe_industry:
                yoe_industry_info.append([self.recog_and_calculate_time(i),self.recog_position(i)])
        return yoe_industry_info
        

    def clean_skills(self):
        s_skills = self.data[self.id]["skills"]
        if s_skills == "None":
            return []
        else:
            # split the sentences and store in the list (can be used for deducting the classification of words)
            sentences = nltk.sent_tokenize(s_skills)
            # store cleaned sentences
            cleaned_skills = []
            # clean data
            for i in range(len(sentences)):
                review = sentences[i].replace("etc.","").replace("e.g.","").replace("i.e.","")
                # only keep letters, + and - in the original passage
                review = re.sub('[^a-zA-Z+-]'," ",review)
                review = review.replace(" one "," ").replace(" two "," ").replace(" three "," ").replace(" four "," ").replace(" five "," ").replace(" six "," ").replace(" seven "," ").replace(" eight "," ").replace(" nine "," ").replace(" ten "," ")
                review = review.lower()
                review = review.split()
                # delete stop words and transfer words to unified format
                review = [word for word in review if not word in set(stopwords.words("english"))]
                review = " ".join(review)
                doc = nlp(review)
                cleaned_skills.append(" ".join([token.lemma_ for token in doc]))
            # return a list that contains cleaned sentences
            return cleaned_skills

    def clean_work_experiences(self):
        s_work_exp = self.data[self.id]["working_experiences"]
        if s_work_exp == "None":
            return []
        else:
            # split the sentences and store in the list (can be used for deducting the classification of words)
            sentences = nltk.sent_tokenize(s_work_exp)
            # store cleaned sentences
            cleaned_work_exp = []
            # clean data
            for i in range(len(sentences)):
                review = sentences[i].replace("etc.","").replace("e.g.","").replace("i.e.","")
                # only keep letters, + and - in the original passage
                review = re.sub('[^a-zA-Z+-]'," ",review)
                review = review.replace(" one "," ").replace(" two "," ").replace(" three "," ").replace(" four "," ").replace(" five "," ").replace(" six "," ").replace(" seven "," ").replace(" eight "," ").replace(" nine "," ").replace(" ten "," ")
                review = review.lower()
                review = review.split()
                # delete stop words and transfer words to unified format
                review = [word for word in review if not word in set(stopwords.words("english"))]
                review = " ".join(review)
                doc = nlp(review)
                cleaned_work_exp.append(" ".join([token.lemma_ for token in doc]))
            # return a list that contains cleaned sentences
            return cleaned_work_exp
    
    def clean_project_experiences(self):
        s_project_exp = self.data[self.id]["project_experiences"]
        if s_project_exp == "None":
            return []
        else:
            # split the sentences and store in the list (can be used for deducting the classification of words)
            sentences = nltk.sent_tokenize(s_project_exp)
            # store cleaned sentences
            cleaned_project_exp = []
            # clean data
            for i in range(len(sentences)):
                review = sentences[i].replace("etc.","").replace("e.g.","").replace("i.e.","")
                # only keep letters, + and - in the original passage
                review = re.sub('[^a-zA-Z+-]'," ",review)
                review = review.replace(" one "," ").replace(" two "," ").replace(" three "," ").replace(" four "," ").replace(" five "," ").replace(" six "," ").replace(" seven "," ").replace(" eight "," ").replace(" nine "," ").replace(" ten "," ")
                review = review.lower()
                review = review.split()
                # delete stop words and transfer words to unified format
                review = [word for word in review if not word in set(stopwords.words("english"))]
                review = " ".join(review)
                doc = nlp(review)
                cleaned_project_exp.append(" ".join([token.lemma_ for token in doc]))
            # return a list that contains cleaned sentences
            return cleaned_project_exp

    def int_store_info(self):
        inner_info = {
            "Name":self.data[self.id]['name'],
            "Country&City":self.data[self.id]["Country&City"],
            "Work_Autho":self.data[self.id]["Work_Autho"],
            "Degree&Major":self.clean_degree_and_major(),
            "YOE&Industry":self.clean_yoe_industry(),
            "skills":self.clean_skills(),
            "working_experiences":self.clean_work_experiences(),
            "project_experiences":self.clean_project_experiences(),
            "posting_history":self.data[self.id]["posting_history"]
        }
        cleaned_info = {self.id:{self.id:inner_info}}
        # this step can be changed to other manipulation that can do storage
        return inner_info


In [20]:
final_dict = {}
c = 0
for keyID in data.keys():
    try:
        info = clean_candidate_profile(data=data,id=keyID).int_store_info()
        final_dict[keyID] = info
        c=c+1
    except:
        print(keyID)
        break

final_dict

{'10000': {'Name': 'lindsey weedon',
  'Country&City': 44,
  'Work_Autho': 'None',
  'Degree&Major': [[14, ['business management', 'management', 'business']]],
  'YOE&Industry': [[123, ['marketing manager']],
   [365, ['manager']],
   [396, ['manager']],
   [303, ['marketing manager']],
   [395, ['marketing manager']],
   [853, ['founder']],
   [365, ['events manager']],
   [61, ['marketing manager']],
   [853, ['marketing specialist']],
   [123, ['manager']],
   [577, ['coordinator']]],
  'skills': [],
  'working_experiences': ['marketing contractor responsibilitie global adsense - small - medium publisher marketing lead global marketing strategy line adsense business product priority drive acquisition growth',
   'act subject matter expert adsense marketing collaborating multiple stakeholder write narrative provide strategic guidance channel owner website blog email social medium youtube seo pay',
   'work closely product sale go - to - market team align consult wide commercialisatio

In [21]:
with open("candidate_profile.json","w") as f:
    json.dump(final_dict,f)

In [22]:
# example 1
data["10010"]

{'name': 'none',
 'Country&City': 65,
 'Work_Autho': 'None',
 'Degree&Major': 'university of mumbai bachelor leadership training',
 'YOE&Industry': 'None',
 'skills': 'None',
 'working_experiences': "at qbr, sales events etc.\r\n•   enable regional growth by supporting sales cycle and drive license (land-expand-renew) and services revenue.\r\n\r\ntrainings\r\nprofessional services & pre sales:\r\n•   general management of apac consulting services including people,\r\nleading through change\r\npractice, delivery, customer success and p&l|communication\r\n•   provide governance across projects, teams and bus, conduct qa & guide\r\npmo.\r\nken blanchard's situational\r\n•   steer discovery workshops, build proof-of-concepts and present value-\r\nleadership slii\r\nbased proposals\r\n\r\nstephen covey's 7 habits of process design & solution architecture:\r\nhighly effective people\r\n•   define & design an enterprise-wide demand planning, replenishment\r\nplanning and s&op process and solu

In [23]:
# example 1
final_dict['10010']

{'Name': 'none',
 'Country&City': 65,
 'Work_Autho': 'None',
 'Degree&Major': [[14, ['leadership', 'leadership training']]],
 'YOE&Industry': [],
 'skills': [],
 'working_experiences': ['qbr sales event',
  'enable regional growth support sale cycle drive license land - expand - renew service revenue',
  'trainings professional service pre sale general management apac consulting service include people lead change practice delivery customer success p l communication provide governance across project team bus conduct qa guide pmo',
  'ken blanchard situational steer discovery workshop build proof - of - concept present value- leadership slii base proposal stephen covey habit process design solution architecture highly effective people define design enterprise - wide demand planning replenishment plan op process solution',
  'conduct design workshop business process requirement to-'],
 'project_experiences': [],
 'posting_history': []}

In [24]:
# example 2
data["10086"]

{'name': 'alec test sample',
 'Country&City': 1,
 'Work_Autho': 'None',
 'Degree&Major': 'None',
 'YOE&Industry': 'testjustfortest test engineer 2021-09-27 2021-10-24',
 'skills': 'None',
 'working_experiences': 'None',
 'project_experiences': 'None',
 'posting_history': []}

In [25]:
# example 2
final_dict["10086"]

{'Name': 'alec test sample',
 'Country&City': 1,
 'Work_Autho': 'None',
 'Degree&Major': [],
 'YOE&Industry': [[27, ['engineer']]],
 'skills': [],
 'working_experiences': [],
 'project_experiences': [],
 'posting_history': []}

In [26]:
# example 3
data["10100"]

{'name': 'shanan delp',
 'Country&City': 1,
 'Work_Autho': 'None',
 'Degree&Major': 'university of california bachelor american studies',
 'YOE&Industry': 'dialpad group product manager, ai products 2021-01-01 2021-01-02|slack group product manager 2019-06-01 2021-02-01|instagram product manager 2018-04-01 2019-05-31|brit + co vp product 2015-05-01 2018-04-01|matter mentor 2014-01-01 2017-01-01|bleacher report vp product + design 2011-03-01 2014-03-01|flickr director of product development 2007-12-01 2011-02-28|yahoo product manager 2004-08-01 2007-01-01|leapfrog enterprises game production 2002-08-01 2004-08-01',
 'skills': 'None',
 'working_experiences': 'making meaning of all of our customers communication, using ai (voice, meetings, text, customer channels). these features are still nascent, and my team\'s goal is to mainstream them in dialpad\'s cloud communications\r\nplatform. i work with our technologists, researchers and customers to use\r\nspeech recognition and ai to tie tog

In [27]:
# example 3
final_dict['10100']

{'Name': 'shanan delp',
 'Country&City': 1,
 'Work_Autho': 'None',
 'Degree&Major': [[13, ['study', 'american study']]],
 'YOE&Industry': [[1, ['product manager']],
  [611, ['product manager']],
  [425, ['product manager']],
  [1066,
   ['line cook',
    'quality control analyst',
    'railroad conductors and yardmaster',
    'adult basic education, adult secondary education, and english as a second language instructor',
    'telecommunications equipment installers and repairers, except line installer',
    'rehabilitation counselor',
    'airline pilots, copilots, and flight engineer',
    'counter and rental clerk',
    'cooks, private household',
    'probation officers and correctional treatment specialist',
    'control and valve installers and repairers, except mechanical door',
    'operations coordinator',
    'computer science teachers, postsecondary',
    'community food project worker',
    'coil winders, tapers, and finisher',
    'coo',
    'computer network support specia

In [28]:
## potential questions need to pay attention
# 1. FOR MAJOR DATABASE
# 1.1 IF NEED TO DO FURTHER CLEAN? (BECAUSE THERE ARE SOME OPTIONS THAT ARE HARD TO DEAL WITH)
# 1.2 LABEL EACH ITEM/ CATEGORY EACH ITEM (LABEL MIGHT BE BETTER) - (CAN BE USED FOR JD PART)
# 2. EXTEND JOB POSITION DATABASE
# 2.1 REDUCE THE POSSIBILITY TO DO APPROXIMATE MATCHING
# 2.2 ALSO LABEL THE JOB POSITION (CAN BE USED TO CALCULATE RELATED WORK EXPERIENCE)
# 3. DO SCHOOL RANKING & FORMER COMPANY PLAY AN IMPORTANT ROLE? （SOME INFO IN THE ORIGINAL DATABASE IS NOT USED）
# 4. HOW TO DEAL WITH THE SITUATION OF MISSING VALUES? (LIKE EXAMPLE 2)(SHOULD WE DELETE THEM DERECTLY?)
# 5. REVIEW OF PAST UNSOLVED QUESTIONS.
# 5.1 IF SKILLSET DATABASE CAN BE FURTHER SUBDIVIDED?
# 5.2 IF SOFTSKILLS PLAY A REALLY IMPORTANT ROLE AS WE IMAGINED? (DIFFERENT WEIGHTS FOR DIFFERENT PARTS OF RESUME)
# 5.3 WEB SCRAP SOFT SKILLS & IDENTIFY UNRECOGNIZED SKILLS (MY WORK) - COULD TRY OTHER PARTS IN O*NET OFFICIAL WEBSITE
# 5.4 IF COULD PROVIDE MORE JD TO FINISH THE CLEANING METHOD OF JD.